# Python with PostgreSQL & PostGIS

<span style="color: blue;">Note: Please always run the complete Jupyter Notebook from the beginning, as object names such as 'sql' and 'gdf' are reused in the code cells.</span>

## Libraries and Settings

In [21]:
# Libraries
import os
import folium
import pandas as pd
import geopandas as gpd
from sqlalchemy import create_engine, text

# Ignore warnings
import warnings
warnings.filterwarnings("ignore")

print(os.getcwd())

/workspaces/python_postgresql_postgis


## Create database connection

In [22]:
# Set up database connection
user = "pgadmin"
password = "geheim"
host = "localhost"
port = "5432"
database = "osm_switzerland"

# Create Connection URL
db_connection_url = "postgresql://" + user + ":" + password +\
                    "@" + host + ":" + port + "/" + database

# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Test database connection
with engine.connect() as connection:
    result = connection.execute(text('SELECT current_database()'))
    print(result.fetchone())

# Dispose the engine
engine.dispose()

('osm_switzerland',)


## List tables in database

In [23]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Open a connection
with engine.connect() as connection:

    # Execute the query
    result = connection.execute(text("""SELECT table_name
                                        FROM information_schema.tables
                                        WHERE table_schema = 'public';"""))
    
    # Fetch and print the results
    for row in result:
        print(row[0])

# Dispose the engine
engine.dispose()

geography_columns
geometry_columns
spatial_ref_sys
planet_osm_polygon
planet_osm_point
planet_osm_line
planet_osm_roads


## Show columns and data types of selected table

In [24]:
## Show columns and data types of selected table
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Define SQL query (ohne Markdown-Formatierung)
sql = """
SELECT
    p.osm_id,
    p.shop,
    p.name,
    ST_Transform(p.way, 4326) AS geom
FROM
    planet_osm_point AS p
WHERE
    p.shop = 'bar';
"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
print(gdf)

Empty GeoDataFrame
Columns: [osm_id, shop, name, geom]
Index: []


## Finde alle Restaurants in Zürich

In [25]:
# SQL query to find all restaurants in Zürich
sql = """
SELECT
    p.osm_id,
    p.amenity,
    p.name,
    ST_Transform(p.way, 4326) AS geom
FROM
    planet_osm_point AS p
WHERE
    p.amenity = 'restaurant'
    AND ST_Within(ST_Transform(p.way, 4326), 
        ST_MakeEnvelope(8.47, 47.34, 8.60, 47.42, 4326));
"""


In [26]:
# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    gdf = gdf.to_crs(epsg=4326)

# Initialize the map
m = folium.Map(location=[47.3769, 8.5417], zoom_start=13, tiles='CartoDBDarkMatter')

# Add GeoJSON to the map
folium.GeoJson(
    gdf,
    name='Restaurants in Zürich',
    popup=folium.GeoJsonPopup(fields=['name', 'amenity'])
).add_to(m)

folium.LayerControl().add_to(m)

# Show the map
m

### Aufgabe 1: Finde alle Supermärkte in Zürich und zeige sie auf einer Karte

In [28]:
# SQL query to find all supermarkets in Zürich
sql = """
SELECT
    p.osm_id,
    p.shop,
    p.name,
    ST_Transform(p.way, 4326) AS geom
FROM
    planet_osm_point AS p
WHERE
    p.shop = 'supermarket'
    AND ST_Within(ST_Transform(p.way, 4326), 
        ST_MakeEnvelope(8.47, 47.34, 8.60, 47.42, 4326));
"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    gdf = gdf.to_crs(epsg=4326)

# Initialize the map
m = folium.Map(location=[47.3769, 8.5417], zoom_start=13, tiles='CartoDBDarkMatter')

# Add GeoJSON to the map
folium.GeoJson(
    gdf,
    name='Supermarkets in Zürich',
    popup=folium.GeoJsonPopup(fields=['name', 'shop'])
).add_to(m)

folium.LayerControl().add_to(m)

# Show the map
m


#### Aufgabe 2: Finde alle Flüsse in der Schweiz und zeige sie auf einer Karte

In [35]:
# SQL query to find all rivers in Switzerland
sql = """
SELECT
    p.osm_id,
    p.waterway,
    ST_Transform(p.way, 4326) AS geom
FROM
    planet_osm_line AS p
WHERE
    p.waterway = 'river';
"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    gdf = gdf.to_crs(epsg=4326)

# Initialize the map
m = folium.Map(location=[46.8182, 8.2275], zoom_start=8, tiles='EsriWorldImagery')

# Add GeoJSON to the map
folium.GeoJson(
    gdf,
    name='Rivers in Switzerland',
    popup=folium.GeoJsonPopup(fields=['waterway'])
).add_to(m)

folium.LayerControl().add_to(m)

# Show the map
m


#### Aufgabe 3: Finde alle Bahnhöfe in Zürich und zeige sie auf einer Karte

In [36]:
# SQL query to find all railway stations in Zürich
sql = """
SELECT
    p.osm_id,
    p.railway,
    p.name,
    ST_Transform(p.way, 4326) AS geom
FROM
    planet_osm_point AS p
WHERE
    p.railway = 'station'
    AND ST_Within(ST_Transform(p.way, 4326), 
        ST_MakeEnvelope(8.47, 47.34, 8.60, 47.42, 4326));
"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    gdf = gdf.to_crs(epsg=4326)

# Initialize the map
m = folium.Map(location=[47.3769, 8.5417], zoom_start=13, tiles='CartoDBDarkMatter')

# Add GeoJSON to the map
folium.GeoJson(
    gdf,
    name='Railway Stations in Zürich',
    popup=folium.GeoJsonPopup(fields=['name', 'railway'])
).add_to(m)

folium.LayerControl().add_to(m)

# Show the map
m


#### Aufgabe 4: Finde alle Hauptstraßen ("primary roads") in Zürich und erstelle eine 500 Meter Pufferzone um sie

In [37]:
# SQL query to find all primary roads in Zürich and create a 500m buffer
sql = """
SELECT 
    1 as group_id,
    ST_Transform(ST_Buffer(p.way::geometry, 500), 4326) AS geom
FROM
    planet_osm_roads AS p
WHERE
    p.highway = 'primary'
    AND ST_Within(ST_Transform(p.way, 4326), 
        ST_MakeEnvelope(8.47, 47.34, 8.60, 47.42, 4326));
"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    gdf = gdf.to_crs(epsg=4326)

# Initialize the map
m = folium.Map(location=[47.3769, 8.5417], zoom_start=13, tiles='CartoDBDarkMatter')

# Add GeoJSON to the map
folium.GeoJson(
    gdf,
    name='Primary Roads Buffer',
).add_to(m)

folium.LayerControl().add_to(m)

# Show the map
m


#### Aufgabe 5: Finde alle Schulen in Zürich und zeige sie auf einer Karte

In [39]:
# SQL query to find all schools in Zürich
sql = """
SELECT
    p.osm_id,
    p.amenity,
    p.name,
    ST_Transform(p.way, 4326) AS geom
FROM
    planet_osm_point AS p
WHERE
    p.amenity = 'school'
    AND ST_Within(ST_Transform(p.way, 4326), 
        ST_MakeEnvelope(8.47, 47.34, 8.60, 47.42, 4326));
"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    gdf = gdf.to_crs(epsg=4326)

# Initialize the map
m = folium.Map(location=[47.3769, 8.5417], zoom_start=13, tiles='CartoDBPositron')

# Add GeoJSON to the map
folium.GeoJson(
    gdf,
    name='Schools in Zürich',
    popup=folium.GeoJsonPopup(fields=['name', 'amenity'])
).add_to(m)

folium.LayerControl().add_to(m)

# Show the map
m


#### Aufgabe 6: Finde alle Polizeiposten in der Schweiz

In [47]:
# SQL query to find all police stations in Switzerland
sql = """
SELECT
    p.osm_id,
    p.amenity,
    p.name,
    ST_Transform(p.way, 4326) AS geom
FROM
    planet_osm_point AS p
WHERE
    p.amenity = 'police';
"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.read_postgis(sql, engine, geom_col='geom')

# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    gdf = gdf.to_crs(epsg=4326)

# Print the first few rows of the GeoDataFrame to verify the data
print(gdf[['name', 'amenity']].head())

# Initialize the map
m = folium.Map(location=[46.8182, 8.2275], zoom_start=9, tiles='EsriWorldTopoMap')

# Add GeoJSON to the map using the correct fields from the DataFrame
folium.GeoJson(
    gdf,
    name='Police Stations in Switzerland',
    popup=folium.GeoJsonPopup(fields=['name', 'amenity'])  # 'name' and 'amenity' are present in the DataFrame
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Show the map
m


                           name amenity
0  Polizeiposten St. Margrethen  police
1                Kantonspolizei  police
2      Polizeistation Rorschach  police
3         Kantonspolizei Heiden  police
4         Polizeiposten Oberegg  police


### Jupyter notebook --footer info-- (please always provide this at the end of each notebook)

In [27]:
import os
import platform
import socket
from platform import python_version
from datetime import datetime

print('-----------------------------------')
print(os.name.upper())
print(platform.system(), '|', platform.release())
print('Datetime:', datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
print('Python Version:', python_version())
print('-----------------------------------')

-----------------------------------
POSIX
Linux | 6.5.0-1025-azure
Datetime: 2024-10-06 15:44:18
Python Version: 3.12.1
-----------------------------------
